## Kirby Super Star Proximal Policy Optimization
#### Riley Hora, riho1074
#### Artificial Intelligence-Fall 2023

## Overview
This project experiments with Proximal Policy Optimization (PPO) using Stable Baseline 3 in the environment of Kirby Super Star on Super Nintendo. This game was chosen because it has not been integrated as part of stable-retro. The goal is to get Kirby to beat the first boss, SkiBomber, with a minimal amount of training time. Kirby Super Star's RAM values are extracted to show the PPO algorithm a reward structure for game play. The notebook then explores the effectiveness of PPO in adapting to this game environment with various hyperparameter. Lastly the notebook will analyze the results to understand the performance and gain insights into reinforcement learning.

## Environment and Game Rules
The game environment is Kirby Super Star on Super Nintendo Entertainment System. Kirby is primarily tested on the game state Spring Breeze Stage 1. The game rules are Kirby can walk, jump, fly, breath in, block, among other moves to progress through 2 dimensional platforming levels to defeat the bosses. Breathing in allows Kirby to absorb their opponent, copying their special abilities. Kirby cannot exit the bottom of the screen in most instances or Kirby looses a life.

These values are extracted using gym-retro-integration tool. The values are found by taking specific actions with Kirby and watching to see which RAM values change as expected. For example when Kirby gets hurt a RAM value decreases, which is tracking Kirby's health. Y-Position is not able to be extracted due to the way it is calculated in Kirby with the Super Nintendo. Y-Position is possibly stored in the graphics chip which helps with smooth scrolling. This means there is no way to directly reward Kirby for moving up or down.

RAM Values:\
health - 40137c <u2\
lives - 40137a |u1\
score - 401376 <u2\
xPos - 400988 <u2

Using the integration tool, cumulative points are tracked for specific common game states. Defeating two enemies and flying above the star until time runs out gives Kirby about 700 points. Defeating the SkiBomber boss which is the end goal of this project is about 1945 points. Kirby getting stuck in the Wooden room corner gives about 2800 points. Making it to the next door, hardly increases points up to 2900. If Kirby were to get further in the game than the goal of the project, defeating the AppleTree boss rewards about 12000 points.

Below is a picture of Kirby with maximum lives and score to test if the RAM values are correct.

In [6]:
from IPython.display import Image
Image('RAMScore.jpg')

## Model and Methods
The first model is Brute force algorithm for comparison. Then PPO is chosen because of its ability to learn complex environments with stable exploration.

The methods are changing hyperparameters including number of games being played in parallel, n_steps, batch_size, max_episode_steps and n_epochs.

The purpose of testing is to reduce training time while defeating the SkiBomber boss.

Experiments range from 30 min to 400 min in training time to see if Kirby defeats the SkiBomber boss, how Kirby learns over time, Kirby's furthest position, and place of convergence if there is one.

In [ ]:
# !python3 -m retro.import /home/riley/stable-retro/retro/data/stable/KirbySuperStar-Snes

In [ ]:
import sys
print(sys.executable)
print (sys.version)
# /bin/python3
# 3.10.12 (main, Jun 11 2023, 05:26:28) [GCC 11.4.0]

In [ ]:
import gymnasium as gym
print(gym.__version__)
# 0.29.1

In [ ]:
import retro
print(retro.__version__)
# 0.9.2

In [ ]:
!nvcc --
# nvcc: NVIDIA (R) Cuda compiler driver
# Copyright (c) 2005-2021 NVIDIA Corporation
# Built on Thu_Nov_18_09:45:30_PST_2021
# Cuda compilation tools, release 11.5, V11.5.119
# Build cuda_11.5.r11.5/compiler.30672275_0

In [ ]:
import tensorflow as tf
print(tf.__version__)
# 2.15.0

In [ ]:
# # Brute Force
# !python3 -m retro.examples.brute --game KirbySuperStar-Snes

Brute Force Output:
new best reward -inf => 283.7000024393201\
new best reward 283.7000024393201 => 294.3000025227666\
new best reward 294.3000025227666 => 298.70000249892473\
new best reward 298.70000249892473 => 493.2000013291836\
new best reward 493.2000013291836 => 527.8000025600195\
new best reward 527.8000025600195 => 841.9500029832125

Kirby does not get over the first wall after 586 minutes and does not seem close to completing that challenge.

## Problem Solving Procedure
Initially with only a few modifications to the PPO it was able to get Kirby to beat the SkiBomb boss in 67 minutes. The Brute Force algorithm by contrast was not able to get to the boss room after 586 minutes of training.

Experiments start with negative reward values for Kirby running out of health and this results in Kirby avoiding the end of the map where the travel star is located, which takes Kirby to the boss, because there are spots to fall on either side. All negative values are removed to encourage exploration.

Lowering all rewards except score, helps Kirby focus on getting to and defeating the boss for the largest reward. This results in Kirby exploring the boss room and beating the SkiBomber much more quickly, only 36 min to defeat the boss.

More training steps allow for longer training and results in Kirby having a longer 'memory'. Running this experiment at 1000 steps is not enough to beat the boss but increasing steps to 2000 is. Increasing the steps further to 4500 allows Kirby to train past the boss.

Sometimes Kirby focuses on entering and exiting a door to respawn enemies, farming points. Lowering all rewards except score and X-position focus Kirby on exploring and defeating the boss. These changes result in the final scenario reward values allowing Kirby to beat the boss in 26 min.
Reward Scenario:
health": 0.05
"lives": 5.0
"score": 6.0
"xPos" : 0.1

Increasing n_steps allowed the PPO to learn more complex environments. Increasing ent_coef from .01 to .015 ecourages slightly more random movement.

Letting the algorithm run for a long period without a dropout rate or other regularization techniques caused over fitting. Kirby would end up flying just above the travel star and not land on the star, which would transport Kirby to the boss room.

Adding a dropout rate through custom Cnn policy layers prevents over-fitting that can be seen below, where all Kirbys are constantly flying.

With the code below, without a dropout rate, Kirby is able to defeat the boss in 10 minutes.

Hyperparameters:\
max_episode_steps=3500\
policy="CnnPolicy",\
env=venv,\
learning_rate=lambda f: f * 2.5e-4,\
n_steps=128, # started at 128 trying, 256, 512 , 1024\
batch_size=1024, # started at 32 success at 128\
n_epochs=15, # started at 4\
gamma=0.99, # starts at 0.99\
gae_lambda=0.95,\
clip_range=0.1,\
ent_coef=0.015,\
verbose=1,\
total_timesteps=100_000_000,\
log_interval=1,

## Trouble Shooting
It took three days of troubleshooting Python, Gymnasium, Tensor Flow and Retro to finally get code running. Landing on the most current and compatible versions ended up working along with exporting the correct paths in the Windows Server for Linux. In the future using a virtual environment will help set up a project like this more quickly and without the risk of ruining other projects through changes in directory paths, default programs and VS code set up. Running more than 20 games in parallel  resulted in crashing so 16 was chosen for stability.

In [ ]:
# Modified from Stable-Retro examples

# """
# Train an agent using Proximal Policy Optimization from Stable Baselines 3
# """

# import argparse
# import retro
# import gymnasium as gym
# import numpy as np
# import imageio
# import os
# from gymnasium.wrappers.time_limit import TimeLimit
# from stable_baselines3 import PPO
# from stable_baselines3.common.atari_wrappers import ClipRewardEnv, WarpFrame
# from stable_baselines3.common.vec_env import (
#     SubprocVecEnv,
#     VecFrameStack,
#     VecTransposeImage,
# )

# def save_frames_as_gif(frames, path='./', filename='gym_animation.gif'):
#     # Save a list of frames as a GIF
#     with imageio.get_writer(os.path.join(path, filename), mode='I') as writer:
#         for frame in frames:
#             writer.append_data(frame)


# class StochasticFrameSkip(gym.Wrapper):
#     def __init__(self, env, n, stickprob):
#         gym.Wrapper.__init__(self, env)
#         self.n = n
#         self.stickprob = stickprob
#         self.curac = None
#         self.rng = np.random.RandomState()
#         self.supports_want_render = hasattr(env, "supports_want_render")

#     def reset(self, **kwargs):
#         self.curac = None
#         return self.env.reset(**kwargs)

#     def step(self, ac):
#         terminated = False
#         truncated = False
#         totrew = 0
#         for i in range(self.n):
#             # First step after reset, use action
#             if self.curac is None:
#                 self.curac = ac
#             # First substep, delay with probability=stickprob
#             elif i == 0:
#                 if self.rng.rand() > self.stickprob:
#                     self.curac = ac
#             # Second substep, new action definitely kicks in
#             elif i == 1:
#                 self.curac = ac
#             if self.supports_want_render and i < self.n - 1:
#                 ob, rew, terminated, truncated, info = self.env.step(
#                     self.curac,
#                     want_render=False,
#                 )
#             else:
#                 ob, rew, terminated, truncated, info = self.env.step(self.curac)
#             totrew += rew
#             if terminated or truncated:
#                 break
#         return ob, totrew, terminated, truncated, info


# def make_retro(*, game, state=None, max_episode_steps=4500, **kwargs): # started at 4500
#     if state is None:
#         state = retro.State.DEFAULT
#     env = retro.make(game, state, **kwargs)
#     env = StochasticFrameSkip(env, n=4, stickprob=0.25)
#     if max_episode_steps is not None:
#         env = TimeLimit(env, max_episode_steps=max_episode_steps)
#     return env


# def wrap_deepmind_retro(env):
#     """
#     Configure environment for retro games, using config similar to DeepMind-style Atari in openai/baseline's wrap_deepmind
#     """
#     env = WarpFrame(env)
#     env = ClipRewardEnv(env)
#     return env


# def main():
#     parser = argparse.ArgumentParser()
#     parser.add_argument("--game", default="KirbySuperStar-Snes")
#     parser.add_argument("--state", default=retro.State.DEFAULT)
#     parser.add_argument("--scenario", default=None)
#     args = parser.parse_args()

#     def make_env():
#         env = make_retro(game=args.game, render_mode="human", state=args.state, scenario=args.scenario)
#         env = wrap_deepmind_retro(env)
#         return env

#     venv = VecTransposeImage(VecFrameStack(SubprocVecEnv([make_env] * 16), n_stack=4))
#     model = PPO(
#         policy="CnnPolicy",
#         env=venv,
#         learning_rate=lambda f: f * 2.5e-4,
#         n_steps=256, # started at 128 , 256 option, 512 option, 1024 for longer levels?
#         batch_size=1024, # started at 32 success at 128
#         n_epochs=15, # started at 4
#         gamma=0.99, # starts at 0.99
#         gae_lambda=0.95,
#         clip_range=0.1,
#         ent_coef=0.015,
#         verbose=1,
#     )
#     model.learn(
#         total_timesteps=100_000_000,
#         log_interval=1,
#     )

# if __name__ == "__main__":
#     main()

In [ ]:
# PPO example that I modified next
!python3 -m retro.examples.ppo --game KirbySuperStar-Snes

## Results Summary
In summary the brute force algorithm resulted in Kirby not getting over the first part of the environment, never mind beating the boss. For PPO, adjusting the number of parallel games being played, n_steps, batch_size, dropout rate and n_epochs all allowed the system to utilize more memory and train more quickly. Interpreting the experiments shows training time to defeat the SkiBomber boss started at 67 minutes with the example PPO algorithm built into stable-retro. After all additions and hyperparameter adjustments the PPO algorithm beat the SkiBomber boss in less than 10 minutes.

Below are links to videos showing Kirby successfully learning how to beat the SkiBomber boss and Kirby learning how to beat the boss on many parallel runs.

In [3]:
from IPython.display import Video
Video("Overfitting.MOV")
# Kirby overfitting to above the star, afraid to fall down and loose a life.

In [4]:
Video("OverfittingAtBoss.mov")
# Again overfitting to the boss room, avoiding loosing a life but does not defeat the boss.

In [5]:
Video("ProgressWDropOut.mov")
# With a dropout rate Kirby continually explores and does not overfit.

Here are the last outputs from a 700 min run without a dropout rate that converged above the star.

-----------------------------------------\
 time:                                
    fps                  | 163         |\
    iterations           | 834         |\
    time_elapsed         | 41770       |\
    total_timesteps      | 6832128     |\
 train:                               
    approx_kl            | 0.012850003 |\
    clip_fraction        | 0.395       |\
    clip_range           | 0.1         |\
    entropy_loss         | -6.64       |\
    explained_variance   | 0.988       |\
    learning_rate        | 0.000241    |\
    loss                 | 0.0504      |\
    n_updates            | 12495       |\
    policy_gradient_loss | -0.0101     |\
    value_loss           | 0.421       |\
-----------------------------------------\
-----------------------------------------\
 time:                                 
    fps                  | 163          |\
    iterations           | 835          |\
    time_elapsed         | 41817        |\
    total_timesteps      | 6840320      |\
 train:                                
    approx_kl            | 0.0148497885 |\
    clip_fraction        | 0.401        |\
    clip_range           | 0.1          |\
    entropy_loss         | -6.61        |\
    explained_variance   | 0.974        |\
    learning_rate        | 0.000241     |\
    loss                 | 0.135        |\
    n_updates            | 12510        |\
    policy_gradient_loss | -0.00731     |\
    value_loss           | 0.711        |\
-----------------------------------------\
-----------------------------------------\
 time:                                
    fps                  | 163         |\
    iterations           | 836         |\
    time_elapsed         | 41865       |\
    total_timesteps      | 6848512     |\
 train:                               
    approx_kl            | 0.010514304 |\
    clip_fraction        | 0.383       |\
    clip_range           | 0.1         |\
    entropy_loss         | -6.62       |\
    explained_variance   | 0.989       |\
    learning_rate        | 0.000241    |\
    loss                 | 0.0826      |\
    n_updates            | 12525       |\
    policy_gradient_loss | -0.00567    |\
    value_loss           | 0.398       |\
\-----------------------------------------


## Discussion
At first extracting Kirby values was difficult due to gym-retro-integration crashing. Once current versions were installed gathering RAM values for this specific game went smoothly. Picking a game of interest helped keep this beginning process exciting.

This project met the original goal of helping Kirby beat the SkiBomber Boss in less training time. Watching many games run in parallel is an entertaining way to understand machine learning algorithms.

In the future adding more models for comparison would be interesting. Being more diligent in recording data would have helped with organizing the findings from this research. Adding code to graph the performance over time, similar to other projects this semester, would give a clearer indication of when performance was optimal. This would have helped make it more clear which hyperparameter effect performance. This would also help visualize when the overfitting is occurring in some test runs.

Rendering the games in rgb mode to train faster and save best runs as gif to share more easily would have further reduced the training time.

References

    Farama Foundation. “Developing with Stable Retro.” Stable Retro Documentation, Farama Foundation, n.d., https://stable-retro.farama.org/developing/.

    Farama Foundation. “Gymnasium.” GitHub, GitHub Repository, Farama Foundation, n.d., https://github.com/Farama-Foundation/Gymnasium.

    Farama Foundation. “Gymnasium API.” Gymnasium API Documentation, Farama Foundation, n.d., https://gymnasium.farama.org/api/env.

    Farama Foundation. “Stable Retro.” GitHub, GitHub Repository, Farama Foundation, n.d., https://github.com/Farama-Foundation/stable-retro#installation.

    HAL Laboratory. Kirby Super Star. Nintendo, 1996. Video Game.

    OpenAI. “Baselines.” GitHub, GitHub Repository, OpenAI, n.d., https://github.com/openai/baselines.